# Pairplot: 9 Delta Features
**Dự án: Giám sát Biến động Rừng tỉnh Cà Mau**

In [ ]:
import sys
from pathlib import Path
sys.path.insert(0, str(Path.cwd().parent / 'src'))

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import warnings
warnings.filterwarnings('ignore')

# Set Times New Roman font for all text
plt.rcParams['font.family'] = 'Times New Roman'
plt.rcParams['font.size'] = 30
plt.rcParams['axes.labelsize'] = 30
plt.rcParams['axes.titlesize'] = 30
plt.rcParams['xtick.labelsize'] = 20
plt.rcParams['ytick.labelsize'] = 20

sns.set_style("whitegrid")
print("Setup completed!")

In [ ]:
from core.data_loader import DataLoader
from core.feature_extraction import FeatureExtraction
from config import FEATURE_NAMES, PLOTS_DIR

# Load data
loader = DataLoader()
data = loader.load_all()
transform = loader.metadata['s2_before']['transform']

# Extract 27-feature stack
extractor = FeatureExtraction()
feature_stack, valid_mask = extractor.extract_features(
    data['s2_before'], data['s2_after'],
    data['s1_before'], data['s1_after']
)
print(f"Feature stack: {feature_stack.shape}")

In [11]:
# 9 Delta features (original names in feature stack)
DELTA_FEATURES_ORIG = [
    'S2_delta_B4', 'S2_delta_B8', 'S2_delta_B11', 'S2_delta_B12',
    'S2_delta_NDVI', 'S2_delta_NBR', 'S2_delta_NDMI',
    'S1_delta_VV', 'S1_delta_VH'
]

# Display names (without S1/S2 prefix)
DELTA_FEATURES_DISPLAY = [
    'ΔB4', 'ΔB8', 'ΔB11', 'ΔB12',
    'ΔNDVI', 'ΔNBR', 'ΔNDMI',
    'ΔVV', 'ΔVH'
]

# Class labels in Vietnamese (order: 0, 1, 2, 3)
CLASS_NAMES = ['Rừng ổn định', 'Mất rừng', 'Phi rừng', 'Phục hồi rừng']
CLASS_COLORS = ['#02734C', '#E60001', '#FFD37F', '#03C5FF']  # Green, Red, Yellow, Blue

# Extract pixel values at 2630 sample points
n_features, height, width = feature_stack.shape
pixel_data = []

for _, row in data['ground_truth'].iterrows():
    col, row_idx = ~transform * (row['x'], row['y'])
    col, row_idx = int(round(col)), int(round(row_idx))
    
    if 0 <= col < width and 0 <= row_idx < height:
        values = feature_stack[:, row_idx, col]
        if not (np.isnan(values).any() or np.isinf(values).any()):
            record = {'label': int(row['label'])}
            for i, name in enumerate(FEATURE_NAMES):
                record[name] = values[i]
            pixel_data.append(record)

df = pd.DataFrame(pixel_data)
print(f"Extracted {len(df)} / 2630 points")

Extracted 2630 / 2630 points


In [12]:
# Prepare data for pairplot
df_plot = df[['label'] + DELTA_FEATURES_ORIG].copy()

# Rename columns to display names
rename_map = dict(zip(DELTA_FEATURES_ORIG, DELTA_FEATURES_DISPLAY))
df_plot = df_plot.rename(columns=rename_map)

# Map labels to Vietnamese class names
df_plot['Các lớp'] = df_plot['label'].map(lambda x: CLASS_NAMES[x])

# Create pairplot (corner=False to show all labels including ΔB4 on y-axis)
g = sns.pairplot(
    df_plot,
    vars=DELTA_FEATURES_DISPLAY,
    hue='Các lớp',
    hue_order=CLASS_NAMES,
    palette=CLASS_COLORS,
    diag_kind='kde',
    plot_kws={'alpha': 0.5, 's': 15, 'edgecolor': None},
    diag_kws={'alpha': 0.7, 'linewidth': 1.5},
    corner=True,
    height=2.5
)

# Set font for all labels
for ax in g.axes.flatten():
    if ax is not None:
        ax.set_xlabel(ax.get_xlabel(), fontsize=30, fontfamily='Times New Roman')
        ax.set_ylabel(ax.get_ylabel(), fontsize=30, fontfamily='Times New Roman')
        ax.tick_params(labelsize=16)

# Title
g.figure.suptitle('Pairplot 9 đặc trưng Delta - Giám sát biến động rừng Cà Mau', 
                  y=1.02, fontsize=36, fontfamily='Times New Roman', fontweight='bold')

# Make legend much bigger
g._legend.set_title('Lớp')
plt.setp(g._legend.get_title(), fontsize=40, fontfamily='Times New Roman', fontweight='bold')
plt.setp(g._legend.get_texts(), fontsize=36, fontfamily='Times New Roman')

# Make legend markers bigger with black edge
for handle in g._legend.legend_handles:
    if hasattr(handle, 'set_sizes'):
        handle.set_sizes([300])
        handle.set_edgecolors('black')
        handle.set_linewidths(1.5)
    elif hasattr(handle, 'set_markersize'):
        handle.set_markersize(20)
        handle.set_markeredgecolor('black')
        handle.set_markeredgewidth(1.5)

plt.tight_layout()
plt.show()

In [13]:
# Save PNG
PLOTS_DIR.mkdir(parents=True, exist_ok=True)
output_path = PLOTS_DIR / 'pairplot_delta_features.png'
g.savefig(output_path, dpi=300, bbox_inches='tight', facecolor='white')
print(f"Saved: {output_path}")

Saved: d:\ninhhaidang\25-26_HKI_DATN_21021411_DangNH\results\plots\pairplot_delta_features.png
